<a href="https://colab.research.google.com/github/zz-carol/zijingzhou_website/blob/main/school_project/python/cs325/cs325_proj5_extra_credit.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Setup

In [ ]:
from google.colab import drive
!pip install stable-baselines3[extra] gymnasium
!pip install gymnasium[accept-rom-license,atari]
!pip install pyvirtualdisplay
!sudo apt-get install -y python-opengl ffmpeg
!sudo apt-get install -y xvfb
!pip install swig
!pip install gymnasium[box2d]

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 55.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 54.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 39.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 13.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 44.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 184.5/184.5 kB 17.2 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstall

In [ ]:
!sudo apt-get install -y python3-opengl

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  freeglut3 libglu1-mesa
Suggested packages:
  libgle3 python3-numpy
The following NEW packages will be installed:
  freeglut3 libglu1-mesa python3-opengl
0 upgraded, 3 newly installed, 0 to remove and 34 not upgraded.
Need to get 824 kB of archives.
After this operation, 8,092 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 freeglut3 amd64 2.8.1-6 [74.0 kB]
Get:2 http://archive.ubuntu.com/ubuntu jammy/main amd64 libglu1-mesa amd64 9.0.2-1 [145 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy/universe amd64 python3-opengl all 3.1.5+dfsg-1 [605 kB]
Fetched 824 kB in 2s (535 kB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/perl5/Debconf/FrontEnd/Dialog.pm line 78, <> line 

# Car Racer Env

reference: https://gymnasium.farama.org/environments/box2d/car_racing/

In [ ]:
import base64
from IPython import display as ipythondisplay
from pathlib import Path
from gymnasium.wrappers import RecordVideo
import gymnasium as gym
import glob
import io
from IPython.display import HTML
from pyvirtualdisplay import Display
import numpy as np

env = gym.make("CarRacing-v3",
               render_mode="rgb_array",
               domain_randomize=False,
               continuous=False)
env

<TimeLimit<OrderEnforcing<PassiveEnvChecker<CarRacing<CarRacing-v3>>>>>

# DQN

In [ ]:
import gymnasium as gym
from stable_baselines3 import DQN
import torch as th
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.torch_layers import NatureCNN
from stable_baselines3.common.env_util import make_vec_env
from gymnasium.wrappers import RecordVideo
import base64
import glob
import io
from IPython.display import HTML
import IPython.display as ipythondisplay

# create and initialize a car racing environment
train_env = gym.make(
    "CarRacing-v3",
    continuous=False,
    domain_randomize=False,
    render_mode=None
)

# define a custom cnn policy
policy_kwargs = dict(
    features_extractor_class=NatureCNN,
    features_extractor_kwargs=dict(features_dim=256),
    net_arch=[256]
)

# instantiate the agent
dqn = DQN(
    "CnnPolicy",
    train_env,
    policy_kwargs=policy_kwargs,
    learning_rate=5e-5,
    buffer_size=100000,
    learning_starts=10000,
    batch_size=64,
    tau=1.0,
    gamma=0.99,
    train_freq=4,
    target_update_interval=1000,
    verbose=1,
    tensorboard_log="./dqn_carracing_tensorboard/"
)

Using cuda device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Wrapping the env in a VecTransposeImage.


In [ ]:
# train the agent
Timesteps = 5e4  # Keep this low initially; increase for better performance
dqn.learn(total_timesteps=int(Timesteps))

# save the agent
dqn.save("dqn_carracing")

Logging to ./dqn_carracing_tensorboard/DQN_2
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -55.5    |
|    exploration_rate | 0.24     |
| time/               |          |
|    episodes         | 4        |
|    fps              | 95       |
|    time_elapsed     | 41       |
|    total_timesteps  | 4000     |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -56.8    |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 8        |
|    fps              | 99       |
|    time_elapsed     | 80       |
|    total_timesteps  | 8000     |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -60.3    |
|    exploration_rate | 0.05     |
| time/   

In [ ]:
# create a fresh environment for evaluation
eval_env = gym.make(
    "CarRacing-v3",
    continuous=False,
    domain_randomize=False,
    render_mode="rgb_array"
)

# evaluate the agent
mean_reward, std_reward = evaluate_policy(dqn, eval_env, n_eval_episodes=5)
print(f"Mean reward: {mean_reward} +/- {std_reward}")

/usr/local/lib/python3.11/dist-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/gymnasium/wrappers/rendering.py:416: UserWarning: WARN: Unable to save last video! Did you call close()?
  logger.warn("Unable to save last video! Did you call close()?")


Mean reward: 114.04431668370962 +/- 101.46642885696123


In [ ]:
# record video
video_callable = lambda episode_id: True
eval_env = RecordVideo(eval_env, video_folder='./videos_carracing_dqn', episode_trigger=video_callable)

# re-evaluate to record
mean_reward, std_reward = evaluate_policy(dqn, eval_env, n_eval_episodes=3)

# display videos
for i in range(3):
    video_path = glob.glob(f'videos_carracing_dqn/rl-video-episode-{i}.mp4')[0]
    video = io.open(video_path, 'r+b').read()
    encoded = base64.b64encode(video)
    ipythondisplay.display(HTML(data=f'''
        <video width="640" height="480" controls>
            <source src="data:video/mp4;base64,{encoded.decode('ascii')}" type="video/mp4" />
        </video>
    '''))

/usr/local/lib/python3.11/dist-packages/gymnasium/wrappers/rendering.py:283: UserWarning: WARN: Overwriting existing videos at /content/videos_carracing_dqn folder (try specifying a different `video_folder` for the `RecordVideo` wrapper if this is not desired)
  logger.warn(


# Extra DQN Code (Please Ignore)

In [ ]:
import gymnasium as gym
from stable_baselines3 import DQN
import torch as th
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.torch_layers import NatureCNN
from stable_baselines3.common.env_util import make_vec_env
from gymnasium.wrappers import RecordVideo
import base64
import glob
import io
from IPython.display import HTML
import IPython.display as ipythondisplay

# Create and initialize CarRacing environment
train_env = gym.make(
    "CarRacing-v3",
    continuous=False,  # Must be False for DQN
    domain_randomize=False,
    render_mode=None
)

# Define a custom CNN policy
policy_kwargs = dict(
    features_extractor_class=NatureCNN,  # Default CNN used in Atari games
    features_extractor_kwargs=dict(features_dim=256),
    net_arch=[256]
)

# Instantiate the agent
dqn = DQN(
    "CnnPolicy",
    train_env,
    policy_kwargs=policy_kwargs,
    learning_rate=1e-4,
    buffer_size=50000,
    learning_starts=10000,
    batch_size=32,
    tau=1.0,
    gamma=0.99,
    train_freq=4,
    target_update_interval=1000,
    verbose=1,
    tensorboard_log="./dqn_carracing_tensorboard/"
)

Using cuda device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Wrapping the env in a VecTransposeImage.


In [ ]:
# Train the agent
Timesteps = 5e4  # Keep this low initially; increase for better performance
dqn.learn(total_timesteps=int(Timesteps))

# Save the agent
dqn.save("dqn_carracing")

Logging to ./dqn_carracing_tensorboard/DQN_1
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -55      |
|    exploration_rate | 0.24     |
| time/               |          |
|    episodes         | 4        |
|    fps              | 100      |
|    time_elapsed     | 39       |
|    total_timesteps  | 4000     |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -54.3    |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 8        |
|    fps              | 102      |
|    time_elapsed     | 77       |
|    total_timesteps  | 8000     |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -53.1    |
|    exploration_rate | 0.05     |
| time/   

In [ ]:
# Create fresh environment for evaluation
eval_env = gym.make(
    "CarRacing-v3",
    continuous=False,
    domain_randomize=False,
    render_mode="rgb_array"
)

# Evaluate the agent
mean_reward, std_reward = evaluate_policy(dqn, eval_env, n_eval_episodes=5)
print(f"Mean reward: {mean_reward} +/- {std_reward}")

/usr/local/lib/python3.11/dist-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Mean reward: 66.7088245227933 +/- 114.43779750984189


In [ ]:
# Record video
video_callable = lambda episode_id: True
eval_env = RecordVideo(eval_env, video_folder='./videos_carracing_dqn', episode_trigger=video_callable)

# Re-evaluate to record
mean_reward, std_reward = evaluate_policy(dqn, eval_env, n_eval_episodes=3)

# Display videos
for i in range(3):
    video_path = glob.glob(f'videos_carracing_dqn/rl-video-episode-{i}.mp4')[0]
    video = io.open(video_path, 'r+b').read()
    encoded = base64.b64encode(video)
    ipythondisplay.display(HTML(data=f'''
        <video width="640" height="480" controls>
            <source src="data:video/mp4;base64,{encoded.decode('ascii')}" type="video/mp4" />
        </video>
    '''))

/usr/local/lib/python3.11/dist-packages/moviepy/config_defaults.py:1: DeprecationWarning: invalid escape sequence '\P'
  """


In [ ]:
import gymnasium as gym
from stable_baselines3 import DQN
import torch as th
from stable_baselines3.common.env_util import make_vec_env
from stable_baselines3.common.vec_env import DummyVecEnv, VecNormalize
from stable_baselines3.common.evaluation import evaluate_policy
import stable_baselines3

# Create and initialize fresh CarRacing environment
train_env = gym.make(
    "CarRacing-v3",
    render_mode="rgb_array",
    domain_randomize=False,
    continuous=False)

# Define custom CNN architecture for image input
# You can tweak the layers further depending on performance
policy_kwargs = dict(
    features_extractor_class=stable_baselines3.common.torch_layers.NatureCNN,
    features_extractor_kwargs=dict(features_dim=512),
    #net_arch=[dict(qf=[512], pi=[512])],  # optional if using NatureCNN
    activation_fn=th.nn.ReLU
)

# Instantiate the DQN agent
dqn = DQN(
    "CnnPolicy",
    train_env,
    policy_kwargs=policy_kwargs,
    learning_rate=1e-4,  # usually smaller for image inputs
    buffer_size=50000,
    learning_starts=10000,
    batch_size=32,
    tau=1.0,
    gamma=0.99,
    train_freq=1,
    target_update_interval=1000,
    exploration_fraction=0.1,
    exploration_final_eps=0.01,
    verbose=1,
    tensorboard_log="./dqn_car_tensorboard/"
)

Using cuda device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Wrapping the env in a VecTransposeImage.


In [ ]:
# Train the agent
Timesteps = 1e6  # Increase steps for complex environments like CarRacing
dqn.learn(total_timesteps=Timesteps)

# Save the agent
dqn.save("dqn_car_racer")

Logging to ./dqn_car_tensorboard/DQN_1
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -57.5    |
|    exploration_rate | 0.96     |
| time/               |          |
|    episodes         | 4        |
|    fps              | 102      |
|    time_elapsed     | 39       |
|    total_timesteps  | 4000     |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -56.4    |
|    exploration_rate | 0.921    |
| time/               |          |
|    episodes         | 8        |
|    fps              | 101      |
|    time_elapsed     | 78       |
|    total_timesteps  | 8000     |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 1e+03    |
|    ep_rew_mean      | -55      |
|    exploration_rate | 0.881    |
| time/         

In [ ]:
# Create fresh eval env
eval_env = gym.make("CarRacing-v3", render_mode="rgb_array")

# Evaluate the agent
mean_reward, std_reward = evaluate_policy(dqn, eval_env, n_eval_episodes=10)
print(f"Mean reward: {mean_reward} +/- {std_reward}")

In [ ]:
# Setup the wrapper to record the video
from gymnasium.wrappers import RecordVideo
video_callable=lambda episode_id: True
eval_env = RecordVideo(eval_env, video_folder='./videos_car_dqn', episode_trigger=video_callable)

mean_reward, std_reward = evaluate_policy(dqn, eval_env, n_eval_episodes=3)

# Display the video
import io, glob, base64
from IPython.display import HTML, display as ipythondisplay

video0 = io.open(glob.glob('videos_car_dqn/rl-video-episode-0.mp4')[0], 'r+b').read()
encoded0 = base64.b64encode(video0)
ipythondisplay(HTML(data='''
    <video width="640" height="480" controls>
        <source src="data:video0/mp4;base64,{0}" type="video/mp4" />
    </video>
'''.format(encoded0.decode('ascii'))))

In [ ]:
import gymnasium as gym
from stable_baselines3 import DQN
import torch as th
from stable_baselines3.dqn.policies import CnnPolicy
from stable_baselines3.common.env_util import make_vec_env
from stable_baselines3.common.vec_env import DummyVecEnv, VecFrameStack
from stable_baselines3.common.evaluation import evaluate_policy

train_env = gym.make("CarRacing-v2", render_mode="rgb_array", domain_randomize=False, continuous=False)

train_env = make_vec_env(lambda: env, n_envs=1)
train_env = VecFrameStack(train_env, n_stack=4)

dqn_racer = DQN(CnnPolicy, train_env, verbose=1, buffer_size=50000, learning_rate=1e-4, batch_size=32,
            tensorboard_log="./dqn_carracer_tensorboard/", exploration_fraction=0.1,
            exploration_final_eps=0.02, target_update_interval=2500)

dqn_racer.learn(total_timesteps=int(1e5))

# Save the model
dqn_racer.save("dqn_carracer_model")

mean_reward, std_reward = evaluate_policy(dqn_racer, dqn_racer.get_env(), n_eval_episodes=10)
print(f"Mean reward: {mean_reward} +/- {std_reward}")

obs = train_env.reset()
for i in range(1000):
    action, _ = dqn_racer.predict(obs, deterministic=True)
    obs, rewards, done, info = train_env.step(action)
    if done:
        break
train_env.close()

# PPO

In [ ]:
from stable_baselines3 import PPO
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.vec_env import VecFrameStack, DummyVecEnv, VecTransposeImage
from stable_baselines3.common.env_util import make_atari_env
import torch as th
import gymnasium as gym
import numpy as np
import io, glob, base64
from IPython.display import HTML
from gymnasium.wrappers import RecordVideo
from IPython import display as ipythondisplay

In [ ]:
# train the agent
TIMESTEPS = 1e5

# setup training environment
env_train = DummyVecEnv([lambda: gym.make("CarRacing-v3", render_mode="rgb_array")])
env_train = VecTransposeImage(env_train)

# define ppo model with cnn policy
lander_ppo = PPO('CnnPolicy', env_train, verbose=1,
          learning_rate=2.5e-4, gamma=0.99, batch_size=64,
          n_steps=512)


Using cuda device


In [ ]:
# train the model
lander_ppo.learn(total_timesteps=int(TIMESTEPS))

# save the model
lander_ppo.save("car_racing_ppo_model")
env_train.close()

----------------------------
| time/              |     |
|    fps             | 78  |
|    iterations      | 1   |
|    time_elapsed    | 6   |
|    total_timesteps | 512 |
----------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 70          |
|    iterations           | 2           |
|    time_elapsed         | 14          |
|    total_timesteps      | 1024        |
| train/                  |             |
|    approx_kl            | 0.004856301 |
|    clip_fraction        | 0.0881      |
|    clip_range           | 0.2         |
|    entropy_loss         | -4.25       |
|    explained_variance   | -0.0283     |
|    learning_rate        | 0.00025     |
|    loss                 | 0.222       |
|    n_updates            | 10          |
|    policy_gradient_loss | -0.0108     |
|    std                  | 0.998       |
|    value_loss           | 0.862       |
-----------------------------------------

In [ ]:
# evaluate the agent
eval_env = DummyVecEnv([lambda: gym.make("CarRacing-v3", render_mode="rgb_array")])
eval_env = VecTransposeImage(eval_env)
mean_reward, std_reward = evaluate_policy(lander_ppo, eval_env, n_eval_episodes=5)

print(f"Mean reward: {mean_reward} +/- {std_reward}")
eval_env.close()

/usr/local/lib/python3.11/dist-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Mean reward: 733.1695526733995 +/- 90.01429908497204


In [ ]:
from pathlib import Path

video_callable = lambda episode_id: True
video_folder = './videos_car_ppo'

# create video folder
Path(video_folder).mkdir(parents=True, exist_ok=True)

# load trained model
lander_ppo = PPO.load("car_racing_ppo_model")

# record 3 episodes
for ep in range(3):
    eval_env = gym.make("CarRacing-v3", render_mode="rgb_array")
    eval_env = RecordVideo(eval_env, video_folder=video_folder, episode_trigger=video_callable)
    obs, _ = eval_env.reset()
    done = False

    while not done:
        action, _ = lander_ppo.predict(obs, deterministic=True)
        obs, reward, terminated, truncated, _ = eval_env.step(action)
        done = terminated or truncated

    eval_env.close()

# display the 3 videos
for i in range(3):
    video_path = glob.glob(f'{video_folder}/rl-video-episode-{i}.mp4')[0]
    video_data = io.open(video_path, 'r+b').read()
    encoded = base64.b64encode(video_data)
    ipythondisplay.display(HTML(data=f'''
        <video width="640" height="480" controls>
            <source src="data:video/mp4;base64,{encoded.decode('ascii')}" type="video/mp4" />
        </video>
    '''))


IndexError: list index out of range

# Extra PPO Code (Please Ignore)

In [ ]:
# Train the agent
TIMESTEPS = 3e5

# Setup training environment
env_train = DummyVecEnv([lambda: gym.make("CarRacing-v3", continuous=True)])
env_train = VecFrameStack(env_train, n_stack=4)

# Define CNN policy architecture (optional - default CNN usually works well)
policy_net = dict(net_arch=[dict(pi=[256], vf=[256])])

# Instantiate the PPO agent with CNNPolicy
car_racer_ppo = PPO(
    'CnnPolicy',
    env_train,
    verbose=1,
    policy_kwargs=policy_net,
    learning_rate=0.0003,
    gamma=0.99,
    batch_size=64,
    n_steps=2048,
    ent_coef=0.01
)

Using cuda device
Wrapping the env in a VecTransposeImage.


In [ ]:
# Train
car_racer_ppo.learn(total_timesteps=int(TIMESTEPS))

# Save the model
car_racer_ppo.save(f"car_racer_ppo_model")
env_train.close()

-----------------------------
| time/              |      |
|    fps             | 80   |
|    iterations      | 1    |
|    time_elapsed    | 25   |
|    total_timesteps | 2048 |
-----------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 71          |
|    iterations           | 2           |
|    time_elapsed         | 56          |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.008929485 |
|    clip_fraction        | 0.109       |
|    clip_range           | 0.2         |
|    entropy_loss         | -4.25       |
|    explained_variance   | -0.00167    |
|    learning_rate        | 0.0003      |
|    loss                 | 0.159       |
|    n_updates            | 10          |
|    policy_gradient_loss | -0.0104     |
|    std                  | 0.998       |
|    value_loss           | 0.617       |
----------------------------------

In [ ]:
# Evaluation
env_eval = DummyVecEnv([lambda: gym.make("CarRacing-v3", continuous=True, render_mode="rgb_array")])
env_eval = VecFrameStack(env_eval, n_stack=4)
mean_reward, std_reward = evaluate_policy(car_racer_ppo, env_eval, n_eval_episodes=10)

print(f"Mean reward: {mean_reward} +/- {std_reward}")

env_eval.close()


/usr/local/lib/python3.11/dist-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Mean reward: 44.03477197214961 +/- 94.02243317090803


In [ ]:
# Setup the wrapper to record the video
import base64
from IPython import display as ipythondisplay
from pathlib import Path
from gymnasium.wrappers import RecordVideo
import glob
import io
from IPython.display import HTML
from pyvirtualdisplay import Display

video_callable = lambda episode_id: True

eval_env = gym.make("CarRacing-v3", continuous=True, render_mode="rgb_array")
video_folder = './videos_car_racer_ppo'
eval_env = RecordVideo(eval_env, video_folder=video_folder, episode_trigger=video_callable)

from stable_baselines3.common.vec_env import DummyVecEnv, VecFrameStack

eval_env_wrapped = DummyVecEnv([lambda: eval_env])
eval_env_wrapped = VecFrameStack(eval_env_wrapped, n_stack=4)

# Load the trained agent
car_racer_ppo = PPO.load(f"car_racer_ppo_model", env=eval_env_wrapped)

# Evaluate agent
mean_reward, std_reward = evaluate_policy(car_racer_ppo, eval_env_wrapped, n_eval_episodes=3)
print("average reward: ", mean_reward)

eval_env.close()

# Display the video
video_files = glob.glob(f'{video_folder}/rl-video-episode-*.mp4')
for i, vf in enumerate(video_files[:3]):
    video_data = io.open(vf, 'r+b').read()
    encoded = base64.b64encode(video_data)
    ipythondisplay.display(HTML(data=f'''
        <video width="640" height="480" controls>
            <source src="data:video/mp4;base64,{encoded.decode('ascii')}" type="video/mp4" />
        </video>
    '''))

Wrapping the env in a VecTransposeImage.


/usr/local/lib/python3.11/dist-packages/moviepy/config_defaults.py:1: DeprecationWarning: invalid escape sequence '\P'
  """


average reward:  97.93517436583836


In [ ]:
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import DummyVecEnv, VecFrameStack, VecTransposeImage
from stable_baselines3.common.env_util import make_atari_env
from stable_baselines3.common.evaluation import evaluate_policy
import gymnasium as gym
from gymnasium.wrappers import RecordVideo
import numpy as np
import os
import base64
from IPython.display import HTML, display
import glob
import io

# Create CarRacing environment
env_name = "CarRacing-v2"
env = gym.make(env_name, render_mode="rgb_array", continuous=True)
env = RecordVideo(env, video_folder="./videos_car_racing_ppo", episode_trigger=lambda e: True)

# Wrap the environment (VecEnv + transpose for CNN)
env = DummyVecEnv([lambda: env])
env = VecTransposeImage(env)  # This is important for CNN-based policies

# Define PPO model with CNNPolicy
car_ppo = PPO("CnnPolicy", env, verbose=1,
              learning_rate=0.0003,
              n_steps=2048,
              batch_size=64,
              gamma=0.99,
              gae_lambda=0.95,
              clip_range=0.2)

# Train the agent
car_ppo.learn(total_timesteps=300000)  # You can adjust this

# Save the model
car_ppo.save("car_racing_ppo_model")

# Evaluate
mean_reward, std_reward = evaluate_policy(car_ppo, env, n_eval_episodes=5)
print(f"CarRacing PPO - Mean reward: {mean_reward} +/- {std_reward}")

# Close environment
env.close()

# === DISPLAY VIDEO ===
def display_videos(video_path="./videos_car_racing_ppo"):
    mp4list = glob.glob(f"{video_path}/*.mp4")
    for i, mp4 in enumerate(mp4list[:3]):  # Show up to 3 videos
        video = io.open(mp4, 'r+b').read()
        encoded = base64.b64encode(video)
        display(HTML(data=f'''
            <video width="640" height="480" controls>
                <source src="data:video/mp4;base64,{encoded.decode('ascii')}" type="video/mp4" />
            </video>
        '''))

display_videos()


In [ ]:
# Setup the wrapper to record the video
video_callable = lambda episode_id: True

eval_env = gym.make("CarRacing-v3", render_mode="rgb_array")
eval_env = RecordVideo(eval_env, video_folder='./videos_car_ppo', episode_trigger=video_callable)

# Load trained agent
lander_ppo = PPO.load("car_racing_ppo_model")

obs, _ = eval_env.reset()
done = False
while not done:
    action, _ = lander_ppo.predict(obs, deterministic=True)
    obs, reward, terminated, truncated, _ = eval_env.step(action)
    done = terminated or truncated

eval_env.close()

# Display recorded video
video_path = glob.glob('videos_car_ppo/rl-video-episode-0.mp4')[0]
video = io.open(video_path, 'r+b').read()
encoded = base64.b64encode(video)
ipythondisplay.display(HTML(data=f'''
    <video width="640" height="480" controls>
        <source src="data:video/mp4;base64,{encoded.decode('ascii')}" type="video/mp4" />
    </video>
'''))

/usr/local/lib/python3.11/dist-packages/gymnasium/wrappers/rendering.py:283: UserWarning: WARN: Overwriting existing videos at /content/videos_car_ppo folder (try specifying a different `video_folder` for the `RecordVideo` wrapper if this is not desired)
  logger.warn(
/usr/local/lib/python3.11/dist-packages/gymnasium/wrappers/rendering.py:416: UserWarning: WARN: Unable to save last video! Did you call close()?
  logger.warn("Unable to save last video! Did you call close()?")
